In [ ]:
# get data from loom

In [2]:
library(Seurat)
library(SeuratDisk)

In [3]:
tab1 <- Connect(filename = 'dev_all.loom', mode = 'r')
tab1

Class: loom
Filename: /home/suresh/adult_mouse_SVZ/La_Manno/dev_all.loom
Access type: H5F_ACC_RDONLY
Attributes: last_modified
Listing:
       name    obj_type   dataset.dims dataset.type_class
      attrs   H5I_GROUP           <NA>               <NA>
  col_attrs   H5I_GROUP           <NA>               <NA>
 col_graphs   H5I_GROUP           <NA>               <NA>
     layers   H5I_GROUP           <NA>               <NA>
     matrix H5I_DATASET 292495 x 31053          H5T_FLOAT
  row_attrs   H5I_GROUP           <NA>               <NA>
 row_graphs   H5I_GROUP           <NA>               <NA>

In [4]:
tab1[['col_attrs']]

Class: H5Group
Filename: /home/suresh/adult_mouse_SVZ/La_Manno/dev_all.loom
Group: /col_attrs
Attributes: last_modified
Listing:
        name    obj_type dataset.dims dataset.type_class
         Age H5I_DATASET       292495         H5T_STRING
       BTSNE H5I_DATASET   2 x 292495          H5T_FLOAT
   CellCycle H5I_DATASET       292495          H5T_FLOAT
      CellID H5I_DATASET       292495         H5T_STRING
   Cell_Conc H5I_DATASET       292495        H5T_INTEGER
   Chemistry H5I_DATASET       292495         H5T_STRING
      ChipID H5I_DATASET       292495         H5T_STRING
       Class H5I_DATASET       292495         H5T_STRING
 ClusterName H5I_DATASET       292495         H5T_STRING
    Clusters H5I_DATASET       292495        H5T_INTEGER
< Printed 10, out of 46>

In [9]:
# Access all gene names
gene.names <- tab1[["row_attrs/Gene"]][]
head(x = gene.names)

[1] "Ptk6"  "Aqp8"  "Neil2" "Lamc1" "Fxyd3" "Lama1"

In [13]:
exp1 <- tab1[["matrix"]][1:292495, 1:31053]
exp1 <- t(exp1)

In [20]:
# head(tab1[["col_attrs/Class"]][])
names(x = tab1[['col_attrs']])

[1] "Age"                "BTSNE"              "CellCycle"         
 [4] "CellID"             "Cell_Conc"          "Chemistry"         
 [7] "ChipID"             "Class"              "ClusterName"       
[10] "Clusters"           "Date_Captured"      "DonorID"           
[13] "DoubletFinderPCA"   "HPF"                "HPF_LogPP"         
[16] "HPF_theta"          "IsCycling"          "Label"             
[19] "Location_E9_E11"    "NCellsCluster"      "NGenes"            
[22] "Num_Pooled_Animals" "PCA"                "PCR_Cycles"        
[25] "Plug_Date"          "Project"            "PseudoAge"         
[28] "PseudoTissue"       "Region"             "SampleID"          
[31] "SampleName"         "Sample_Index"       "Sex"               
[34] "Species"            "Split"              "Strain"            
[37] "Subclass"           "TSNE"               "Target_Num_Cells"  
[40] "Tissue"             "TotalUMI"           "Transcriptome"     
[43] "UMAP"               "UMAP3D"             "cDNA_Lib_Ok"       
[46] "ngperul_cDNA"

In [33]:
# Pull three bits of metadata from the column attributes
attrs <- c("Age", "CellCycle", "CellID", 'Cell_Conc', 'Chemistry', 'ChipID', 'Class', 'ClusterName', 'Clusters', 
           'Date_Captured', 'DonorID', 'IsCycling', 'Label', 'Location_E9_E11', 'NCellsCluster', 'NGenes', 
           'Num_Pooled_Animals', 'Project', 'PseudoAge', 'PseudoTissue', 'Region', 'SampleID', 'SampleName', 'Sample_Index',
           'Sex', 'Species', 'Split', 'Strain', 'Subclass', 'Tissue')
attr.df = c()

for(ii in 1:length(attrs)){
    vec1 = tab1[[paste0("col_attrs/", attrs[ii])]][]
    attr.df = rbind(attr.df, vec1)
}
attr.df = t(attr.df)
colnames(attr.df) = attrs
attr.df <- data.frame(attr.df)
attr.df[1:2,]

Age  CellCycle           CellID                      Cell_Conc Chemistry
[1,] e7.0 0.00456829602558246 10X39_2_A_1:AAACTTGAGAGCAGx 500       v2       
[2,] e7.0 0.0108813928182807  10X39_3_A_1:AAGTTCCTAGCCTAx 500       v2       
     ChipID Class        ClusterName Clusters Date_Captured ⋯ Region SampleID
[1,] 10X39  Gastrulation ParEndo     0        2016-09-30    ⋯ Head   10X39_2 
[2,] 10X39  Gastrulation ParEndo     0        2016-09-30    ⋯ Head   10X39_3 
     SampleName Sample_Index Sex Species Split Strain Subclass         
[1,] G66        SI-3A-B5     ?   Mm      1     CD-1   Parietal endoderm
[2,] G67        SI-3A-C5     ?   Mm      1     CD-1   Parietal endoderm
     Tissue                 
[1,] All (No extraembryonal)
[2,] All (No extraembryonal)

In [41]:
table(attr.df$Region)


Forebrain      Head Hindbrain  Midbrain 
   138419     24026     70781     59269 

In [40]:
table(attr.df$Tissue)


All (No extraembryonal)               Forebrain         ForebrainDorsal 
                  12981                   23386                   49370 
       ForebrainVentral  ForebrainVentroLateral ForebrainVentroThalamic 
                  22642                   17277                   25744 
                   Head               Hindbrain                Midbrain 
                  11045                   70781                   51071 
         MidbrainDorsal         MidbrainVentral 
                   3283                    4915 

In [42]:
rownames(exp1) = gene.names
colnames(exp1) = unlist(attr.df$CellID)
rownames(attr.df) = unlist(attr.df$CellID)

In [45]:
# remove duplicate gene names
genes2 = unique(gene.names)
length(genes2)
exp2 = exp1[match(genes2, gene.names),]
dim(exp2)

[1] 31017

[1]  31017 292495

In [47]:
keepids = which(attr.df$Region %in% c('Forebrain', 'Midbrain', 'Hindbrain'))
seu = CreateSeuratObject(counts = exp2[,keepids], meta.data = attr.df[keepids,])
seu

Warning message:
“Data is of class matrix. Coercing to dgCMatrix.”


An object of class Seurat 
31017 features across 268469 samples within 1 assay 
Active assay: RNA (31017 features, 0 variable features)
 1 layer present: counts

In [48]:
# save
saveRDS(seu, file = 'La_Manno_data.rds')